## Import Libraries - Data

In [22]:
import pandas as pd
import numpy as np
from gensim.models import Word2Vec
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import PCA

#set the max columns to none
pd.set_option('display.max_columns', None)

In [55]:
# Raw data
size = 'demo'
type = 'train'
articles_path = f'./files/parquet/ebnerd_{size}/articles.parquet'
behaviors_path = f'./files/parquet/ebnerd_{size}/{type}/behaviors.parquet'
history_path = f'./files/parquet/ebnerd_{size}/{type}/history.parquet'
df_articles = pd.read_parquet(articles_path)
df_behaviors = pd.read_parquet(behaviors_path)
df_history = pd.read_parquet(history_path)


# Ready embeddings
#embeddings_path = f'./files/parquet/FacebookAI_xlm_roberta_base/xlm_roberta_base.parquet'
embeddings_path = f'./files/parquet/Ekstra_Bladet_word2vec/document_vector.parquet'
df_embeddings = pd.read_parquet(embeddings_path)

In [4]:
print(df_articles.columns)
print(df_articles.shape)
df_articles.head(5)

Index(['article_id', 'title', 'subtitle', 'last_modified_time', 'premium',
       'body', 'published_time', 'image_ids', 'article_type', 'url',
       'ner_clusters', 'entity_groups', 'topics', 'category', 'subcategory',
       'category_str', 'total_inviews', 'total_pageviews', 'total_read_time',
       'sentiment_score', 'sentiment_label'],
      dtype='object')
(11777, 21)


article_id                                       title  \
0     3037230  Ishockey-spiller: Jeg troede jeg skulle dø   
1     3044020            Prins Harry tvunget til dna-test   
2     3057622                 Rådden kørsel på blå plader   
3     3073151                   Mærsk-arvinger i livsfare   
4     3193383              Skød svigersøn gennem babydyne   

                                            subtitle  last_modified_time  \
0  ISHOCKEY: Ishockey-spilleren Sebastian Harts h... 2023-06-29 06:20:57   
1  Hoffet tvang Prins Harry til at tage dna-test ... 2023-06-29 06:21:16   
2  Kan ikke straffes: Udenlandske diplomater i Da... 2023-06-29 06:21:24   
3  FANGET I FLODBØLGEN: Skibsrederens oldebørn må... 2023-06-29 06:21:38   
4  44-årig kvinde tiltalt for drab på ekssvigersø... 2023-06-29 06:22:57   

   premium                                               body  \
0    False  Ambitionerne om at komme til USA og spille ish...   
1    False  Den britiske tabloidavis The Sun fortsætter me...   
2    False  Slingrende spritkørsel. Grove overtrædelser af...   
3    False  To oldebørn af skibsreder Mærsk McKinney Mølle...   
4    False  En 44-årig mormor blev i dag fremstillet i et ...   

       published_time                    image_ids     article_type  \
0 2003-08-28 08:55:00                         None  article_default   
1 2005-06-29 08:47:00  [3097307, 3097197, 3104927]  article_default   
2 2005-10-10 07:20:00                    [3047102]  article_default   
3 2005-01-04 06:59:00  [3067474, 3067478, 3153705]  article_default   
4 2003-09-15 15:30:00                         None  article_default   

                                                 url           ner_clusters  \
0  https://ekstrabladet.dk/sport/anden_sport/isho...                     []   
1  https://ekstrabladet.dk/underholdning/udlandke...  [Harry, James Hewitt]   
2  https://ekstrabladet.dk/nyheder/samfund/articl...                     []   
3  https://ekstrabladet.dk/nyheder/samfund/articl...                     []   
4   https://ekstrabladet.dk/krimi/article3193383.ece                     []   

  entity_groups                                             topics  category  \
0            []  [Kriminalitet, Kendt, Sport, Katastrofe, Mindr...       142   
1    [PER, PER]  [Kriminalitet, Kendt, Underholdning, Personfar...       414   
2            []               [Kriminalitet, Transportmiddel, Bil]       118   
3            []  [Erhverv, Privat virksomhed, Livsstil, Familie...       118   
4            []          [Kriminalitet, Personfarlig kriminalitet]       140   

  subcategory   category_str  total_inviews  total_pageviews  total_read_time  \
0  [327, 334]          sport            NaN              NaN              NaN   
1       [432]  underholdning            NaN              NaN              NaN   
2       [133]        nyheder            NaN              NaN              NaN   
3       [133]        nyheder            NaN              NaN              NaN   
4          []          krimi            NaN              NaN              NaN   

   sentiment_score sentiment_label  
0           0.9752        Negative  
1           0.7084        Negative  
2           0.9236        Negative  
3           0.9945        Negative  
4           0.9966        Negative

In [5]:
print(df_behaviors.columns)
print(df_behaviors.shape)
df_behaviors.head(2)

Index(['impression_id', 'article_id', 'impression_time', 'read_time',
       'scroll_percentage', 'device_type', 'article_ids_inview',
       'article_ids_clicked', 'user_id', 'is_sso_user', 'gender', 'postcode',
       'age', 'is_subscriber', 'session_id', 'next_read_time',
       'next_scroll_percentage'],
      dtype='object')
(24724, 17)


impression_id  article_id     impression_time  read_time  \
0          48401         NaN 2023-05-21 21:06:50       21.0   
1         152513   9778745.0 2023-05-24 07:31:26       30.0   

   scroll_percentage  device_type  \
0                NaN            2   
1              100.0            1   

                                  article_ids_inview article_ids_clicked  \
0  [9774516, 9771051, 9770028, 9775402, 9774461, ...           [9759966]   
1  [9778669, 9778736, 9778623, 9089120, 9778661, ...           [9778661]   

   user_id  is_sso_user  gender  postcode  age  is_subscriber  session_id  \
0    22779        False     NaN       NaN  NaN          False          21   
1   150224        False     NaN       NaN  NaN          False         298   

   next_read_time  next_scroll_percentage  
0            16.0                    27.0  
1             2.0                    48.0

In [6]:
print(df_history.columns)
print(df_history.shape)
df_history.head(2)

Index(['user_id', 'impression_time_fixed', 'scroll_percentage_fixed',
       'article_id_fixed', 'read_time_fixed'],
      dtype='object')
(1590, 5)


user_id                              impression_time_fixed  \
0    13538  [2023-04-27T10:17:43.000000, 2023-04-27T10:18:...   
1    58608  [2023-04-27T18:48:09.000000, 2023-04-27T18:48:...   

                             scroll_percentage_fixed  \
0  [100.0, 35.0, 100.0, 24.0, 100.0, 23.0, 100.0,...   
1  [37.0, 61.0, 100.0, 100.0, 55.0, 100.0, 100.0,...   

                                    article_id_fixed  \
0  [9738663, 9738569, 9738663, 9738490, 9738663, ...   
1  [9739362, 9739179, 9738567, 9739344, 9739202, ...   

                                     read_time_fixed  
0  [17.0, 12.0, 4.0, 5.0, 4.0, 9.0, 5.0, 46.0, 11...  
1  [2.0, 24.0, 72.0, 65.0, 11.0, 4.0, 101.0, 0.0,...

In [11]:
## Specify the path to your text file
file_path = './files/parquet/predictions.txt'

# Initialize lists to store parsed data
keys = []
values = []

# Open the file in read mode
with open(file_path, 'r') as file:
    # Read each line in the file
    for line in file:
        # Strip any leading/trailing whitespace characters
        line = line.strip()
        
        # Extract the key (number before the '[' character)
        key_start = line.find(' ')
        key = int(line[:key_start])
        
        # Extract the value (list of integers inside the brackets)
        value_str = line[key_start:]
        value = [int(num) for num in value_str.strip()[1:-1].split(',')]  # Extract and convert to list of integers
        
        # Append key and value to lists
        keys.append(key)
        values.append(value)

# Create a DataFrame from the lists of keys and values
df = pd.DataFrame({'Key': keys, 'Value': values})



In [4]:
df

Key                                              Value
0         6451339                        [8, 1, 6, 7, 4, 2, 9, 5, 3]
1         6451363                           [5, 4, 3, 7, 6, 8, 1, 2]
2         6451382                                    [1, 5, 3, 4, 2]
3         6451383                [7, 6, 8, 9, 3, 4, 2, 11, 10, 1, 5]
4         6451385                              [5, 3, 2, 4, 7, 6, 1]
...           ...                                                ...
13536705        0  [120, 49, 179, 32, 30, 42, 155, 50, 45, 234, 9...
13536706        0  [248, 62, 36, 2, 152, 199, 241, 235, 155, 160,...
13536707        0  [163, 77, 143, 232, 69, 16, 27, 119, 186, 166,...
13536708        0  [113, 233, 67, 105, 130, 8, 100, 173, 158, 28,...
13536709        0  [142, 17, 248, 67, 201, 159, 163, 219, 22, 40,...

[13536710 rows x 2 columns]

## I will create two tables with embeddings, one will come from df_articles and the other from the other two dfs joined. I will try firstly the embeddings that are provided and more specificaly the word2vec embeddings, in order to create a proof of concept. After that if it is needed i will begin from the raw data to build the embeddings from scratch.

## Pre process df_articles

In [56]:
df_embeddings

article_id                                    document_vector
0          3000022  [0.06542388, -0.047424573, 0.06384871, -0.0014...
1          3000063  [0.028815078, -0.00016637295, 0.055056807, 0.0...
2          3000613  [0.037971217, 0.03392251, 0.027297212, 0.01708...
3          3000700  [0.04652399, 0.0029133065, 0.06280604, -0.0051...
4          3000840  [0.014736942, 0.024067875, 0.0051865038, 0.041...
...            ...                                                ...
125536     9803505  [0.029624538, -0.039833125, -0.03009815, 0.005...
125537     9803510  [-0.0284717, -0.035652492, 0.027552828, -0.018...
125538     9803525  [0.039465133, 0.00079695834, 0.062067263, 0.08...
125539     9803560  [0.0049191406, 0.01373551, 0.020911952, 0.0108...
125540     9803607  [0.0005135782, -0.046943206, 0.054680478, 0.02...

[125541 rows x 2 columns]

In [57]:
df_articles.head()

article_id                                       title  \
0     3037230  Ishockey-spiller: Jeg troede jeg skulle dø   
1     3044020            Prins Harry tvunget til dna-test   
2     3057622                 Rådden kørsel på blå plader   
3     3073151                   Mærsk-arvinger i livsfare   
4     3193383              Skød svigersøn gennem babydyne   

                                            subtitle  last_modified_time  \
0  ISHOCKEY: Ishockey-spilleren Sebastian Harts h... 2023-06-29 06:20:57   
1  Hoffet tvang Prins Harry til at tage dna-test ... 2023-06-29 06:21:16   
2  Kan ikke straffes: Udenlandske diplomater i Da... 2023-06-29 06:21:24   
3  FANGET I FLODBØLGEN: Skibsrederens oldebørn må... 2023-06-29 06:21:38   
4  44-årig kvinde tiltalt for drab på ekssvigersø... 2023-06-29 06:22:57   

   premium                                               body  \
0    False  Ambitionerne om at komme til USA og spille ish...   
1    False  Den britiske tabloidavis The Sun fortsætter me...   
2    False  Slingrende spritkørsel. Grove overtrædelser af...   
3    False  To oldebørn af skibsreder Mærsk McKinney Mølle...   
4    False  En 44-årig mormor blev i dag fremstillet i et ...   

       published_time                    image_ids     article_type  \
0 2003-08-28 08:55:00                         None  article_default   
1 2005-06-29 08:47:00  [3097307, 3097197, 3104927]  article_default   
2 2005-10-10 07:20:00                    [3047102]  article_default   
3 2005-01-04 06:59:00  [3067474, 3067478, 3153705]  article_default   
4 2003-09-15 15:30:00                         None  article_default   

                                                 url           ner_clusters  \
0  https://ekstrabladet.dk/sport/anden_sport/isho...                     []   
1  https://ekstrabladet.dk/underholdning/udlandke...  [Harry, James Hewitt]   
2  https://ekstrabladet.dk/nyheder/samfund/articl...                     []   
3  https://ekstrabladet.dk/nyheder/samfund/articl...                     []   
4   https://ekstrabladet.dk/krimi/article3193383.ece                     []   

  entity_groups                                             topics  category  \
0            []  [Kriminalitet, Kendt, Sport, Katastrofe, Mindr...       142   
1    [PER, PER]  [Kriminalitet, Kendt, Underholdning, Personfar...       414   
2            []               [Kriminalitet, Transportmiddel, Bil]       118   
3            []  [Erhverv, Privat virksomhed, Livsstil, Familie...       118   
4            []          [Kriminalitet, Personfarlig kriminalitet]       140   

  subcategory   category_str  total_inviews  total_pageviews  total_read_time  \
0  [327, 334]          sport            NaN              NaN              NaN   
1       [432]  underholdning            NaN              NaN              NaN   
2       [133]        nyheder            NaN              NaN              NaN   
3       [133]        nyheder            NaN              NaN              NaN   
4          []          krimi            NaN              NaN              NaN   

   sentiment_score sentiment_label  
0           0.9752        Negative  
1           0.7084        Negative  
2           0.9236        Negative  
3           0.9945        Negative  
4           0.9966        Negative

In [58]:
df_articles.isnull().sum()

article_id               0
title                    0
subtitle                 0
last_modified_time       0
premium                  0
body                     0
published_time           0
image_ids              937
article_type             0
url                      0
ner_clusters             0
entity_groups            0
topics                   0
category                 0
subcategory              0
category_str             0
total_inviews         4271
total_pageviews       4271
total_read_time       4271
sentiment_score          0
sentiment_label          0
dtype: int64

In [59]:
#df_articles = df_articles.drop(["image_ids", "total_inviews", "total_pageviews", "total_read_time", "last_modified_time", "published_time", "url"], axis= 1)

df_articles = df_articles[["article_id"]]

In [60]:
df_articles.head()

article_id
0     3037230
1     3044020
2     3057622
3     3073151
4     3193383

In [61]:
df_articles_embeddings = pd.merge(df_articles, df_embeddings, on="article_id") 

In [62]:
df_articles_embeddings.head()

article_id                                    document_vector
0     3037230  [0.017898837, -0.012223162, 0.0117029, 0.03572...
1     3044020  [0.041870505, 0.002982251, 0.07588886, -0.0031...
2     3057622  [0.03602814, -0.004919843, -0.005812604, 0.015...
3     3073151  [0.039754465, -0.014155321, 0.044064052, 0.040...
4     3193383  [0.014357477, -0.07686433, 0.07009871, 0.02835...

In [65]:
df_articles_embeddings = df_articles_embeddings.set_index('article_id')

In [66]:
df_articles_embeddings.head()

document_vector
article_id                                                   
3037230     [0.017898837, -0.012223162, 0.0117029, 0.03572...
3044020     [0.041870505, 0.002982251, 0.07588886, -0.0031...
3057622     [0.03602814, -0.004919843, -0.005812604, 0.015...
3073151     [0.039754465, -0.014155321, 0.044064052, 0.040...
3193383     [0.014357477, -0.07686433, 0.07009871, 0.02835...

In [67]:
def unpack_lists(df, column_name):
    # Create new columns by unpacking lists in the specified column
    unpacked_cols = pd.DataFrame(df[column_name].tolist(), index=df.index)
    # Rename the columns with a prefix based on the original column name
    unpacked_cols = unpacked_cols.add_prefix(column_name + '_')
    # Concatenate the unpacked columns back to the original DataFrame
    df = pd.concat([df, unpacked_cols], axis=1)
    return df

# Specify which columns to process
columns_to_process = ['document_vector']

# Unpack lists in each specified column
for col in columns_to_process:
    df_articles_embeddings = unpack_lists(df_articles_embeddings, col)

In [69]:
df_articles_embeddings.drop('document_vector', axis=1, inplace=True)

In [71]:
df_articles_embeddings.shape

(11777, 300)

## Pre process df_behaviors and df_history

In [24]:
df_behaviors.isnull().sum()

impression_id                 0
article_id                17346
impression_time               0
read_time                     0
scroll_percentage         17482
device_type                   0
article_ids_inview            0
article_ids_clicked           0
user_id                       0
is_sso_user                   0
gender                    22927
postcode                  24363
age                       24107
is_subscriber                 0
session_id                    0
next_read_time              673
next_scroll_percentage     2757
dtype: int64

In [25]:
df_behaviors = df_behaviors.drop(["impression_id","impression_time", "scroll_percentage", "gender", "postcode","age","article_id", "next_read_time", "next_scroll_percentage"], axis=1)

In [26]:
df_behaviors.isnull().sum()

read_time              0
device_type            0
article_ids_inview     0
article_ids_clicked    0
user_id                0
is_sso_user            0
is_subscriber          0
session_id             0
dtype: int64

In [27]:
df_users = pd.merge(df_behaviors, df_history, on="user_id") 

In [28]:
df_users =df_users.drop(["impression_time_fixed"], axis=1)

In [29]:
df_users.head()

read_time  device_type                                 article_ids_inview  \
0       21.0            2  [9774516, 9771051, 9770028, 9775402, 9774461, ...   
1       30.0            1  [9778669, 9778736, 9778623, 9089120, 9778661, ...   
2       45.0            1  [9778369, 9777856, 9778500, 9778021, 9778627, ...   
3       33.0            2  [9776715, 9776406, 9776566, 9776071, 9776808, ...   
4       21.0            2  [9775202, 9776855, 9776688, 9771995, 9776583, ...   

  article_ids_clicked  user_id  is_sso_user  is_subscriber  session_id  \
0           [9759966]    22779        False          False          21   
1           [9778661]   150224        False          False         298   
2           [9777856]   160892        False          False         401   
3           [9776566]  1001055        False          False        1357   
4           [9776553]  1001055        False          False        1358   

                             scroll_percentage_fixed  \
0  [28.0, 17.0, 35.0, 4.0, 77.0, 26.0, 53.0, 59.0...   
1  [100.0, 49.0, 100.0, 100.0, 72.0, 100.0, 85.0,...   
2  [100.0, 20.0, 100.0, 100.0, 100.0, 15.0, 58.0,...   
3  [100.0, 100.0, 39.0, 100.0, 100.0, 97.0, 35.0,...   
4  [100.0, 100.0, 39.0, 100.0, 100.0, 97.0, 35.0,...   

                                    article_id_fixed  \
0  [9738452, 9737521, 9738760, 9733713, 9738777, ...   
1  [9740087, 9741986, 9740591, 9741830, 9742491, ...   
2  [9738557, 9738211, 9736646, 9739342, 9739443, ...   
3  [9738777, 9738663, 9736693, 9738656, 9736689, ...   
4  [9738777, 9738663, 9736693, 9738656, 9736689, ...   

                                     read_time_fixed  
0  [5.0, 4.0, 3.0, 21.0, 18.0, 4.0, 23.0, 3.0, 6....  
1  [18.0, 244.0, 32.0, 36.0, 31.0, 58.0, 65.0, 59...  
2  [583.0, 257.0, 10.0, 396.0, 28.0, 6.0, 3.0, 10...  
3  [35.0, 62.0, 6.0, 48.0, 71.0, 95.0, 6.0, 6.0, ...  
4  [35.0, 62.0, 6.0, 48.0, 71.0, 95.0, 6.0, 6.0, ...

In [30]:
for col in ["is_sso_user", "is_subscriber"]:
    df_users[col] = df_users[col].replace({False: 0, True: 1})

/var/folders/ld/c07vs56s18bc0h2krlvl0myr0000gn/T/ipykernel_25109/3302489445.py:2: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df_users[col] = df_users[col].replace({False: 0, True: 1})


In [31]:
def has_na(x):
    if np.nan in x:
        return True
    else:
        return False

In [32]:
for col in ["article_ids_inview", "scroll_percentage_fixed", "read_time_fixed","article_id_fixed", "article_ids_clicked"]:
    df_users[col+"_nans"] = df_users[col].map(has_na)
    print(df_users[col+"_nans"].unique())

[False]
[False]
[False]
[False]
[False]


## Nans do not exist inside the lists

In [33]:
df_users = df_users.drop(["article_ids_inview_nans", "read_time_fixed_nans", "scroll_percentage_fixed_nans", "article_id_fixed_nans", "article_ids_clicked_nans"], axis=1)

In [34]:
df_users.head()

read_time  device_type                                 article_ids_inview  \
0       21.0            2  [9774516, 9771051, 9770028, 9775402, 9774461, ...   
1       30.0            1  [9778669, 9778736, 9778623, 9089120, 9778661, ...   
2       45.0            1  [9778369, 9777856, 9778500, 9778021, 9778627, ...   
3       33.0            2  [9776715, 9776406, 9776566, 9776071, 9776808, ...   
4       21.0            2  [9775202, 9776855, 9776688, 9771995, 9776583, ...   

  article_ids_clicked  user_id  is_sso_user  is_subscriber  session_id  \
0           [9759966]    22779            0              0          21   
1           [9778661]   150224            0              0         298   
2           [9777856]   160892            0              0         401   
3           [9776566]  1001055            0              0        1357   
4           [9776553]  1001055            0              0        1358   

                             scroll_percentage_fixed  \
0  [28.0, 17.0, 35.0, 4.0, 77.0, 26.0, 53.0, 59.0...   
1  [100.0, 49.0, 100.0, 100.0, 72.0, 100.0, 85.0,...   
2  [100.0, 20.0, 100.0, 100.0, 100.0, 15.0, 58.0,...   
3  [100.0, 100.0, 39.0, 100.0, 100.0, 97.0, 35.0,...   
4  [100.0, 100.0, 39.0, 100.0, 100.0, 97.0, 35.0,...   

                                    article_id_fixed  \
0  [9738452, 9737521, 9738760, 9733713, 9738777, ...   
1  [9740087, 9741986, 9740591, 9741830, 9742491, ...   
2  [9738557, 9738211, 9736646, 9739342, 9739443, ...   
3  [9738777, 9738663, 9736693, 9738656, 9736689, ...   
4  [9738777, 9738663, 9736693, 9738656, 9736689, ...   

                                     read_time_fixed  
0  [5.0, 4.0, 3.0, 21.0, 18.0, 4.0, 23.0, 3.0, 6....  
1  [18.0, 244.0, 32.0, 36.0, 31.0, 58.0, 65.0, 59...  
2  [583.0, 257.0, 10.0, 396.0, 28.0, 6.0, 3.0, 10...  
3  [35.0, 62.0, 6.0, 48.0, 71.0, 95.0, 6.0, 6.0, ...  
4  [35.0, 62.0, 6.0, 48.0, 71.0, 95.0, 6.0, 6.0, ...

## Unpack list in columns

In [35]:
def unpack_lists(df, column_name):
    # Create new columns by unpacking lists in the specified column
    unpacked_cols = pd.DataFrame(df[column_name].tolist(), index=df.index)
    # Rename the columns with a prefix based on the original column name
    unpacked_cols = unpacked_cols.add_prefix(column_name + '_')
    # Concatenate the unpacked columns back to the original DataFrame
    df = pd.concat([df, unpacked_cols], axis=1)
    return df

# Specify which columns to process
columns_to_process = ['article_ids_inview', 'article_ids_clicked', 'scroll_percentage_fixed', 'article_id_fixed', 'read_time_fixed']

# Unpack lists in each specified column
for col in columns_to_process:
    df_users = unpack_lists(df_users, col)


In [36]:
df_users = df_users.drop(columns_to_process, axis=1)

In [37]:
df_users = df_users.set_index('user_id')

In [38]:
df_users

read_time  device_type  is_sso_user  is_subscriber  session_id  \
user_id                                                                   
22779         21.0            2            0              0          21   
150224        30.0            1            0              0         298   
160892        45.0            1            0              0         401   
1001055       33.0            2            0              0        1357   
1001055       21.0            2            0              0        1358   
...            ...          ...          ...            ...         ...   
2053999       35.0            1            0              0      170832   
2053999       89.0            1            0              0      170832   
2060487      123.0            2            0              0      107303   
2060487       73.0            2            0              0      107303   
2096611      107.0            1            0              0       73638   

         article_ids_inview_0  article_ids_inview_1  article_ids_inview_2  \
user_id                                                                     
22779                 9774516               9771051               9770028   
150224                9778669               9778736               9778623   
160892                9778369               9777856               9778500   
1001055               9776715               9776406               9776566   
1001055               9775202               9776855               9776688   
...                       ...                   ...                   ...   
2053999               9775562               9775701               9486486   
2053999               9775347               9678300               9754160   
2060487               9775699               9775722               9774541   
2060487               9772221               9758424               9775699   
2096611               9657528               9769356               9746428   

         article_ids_inview_3  article_ids_inview_4  article_ids_inview_5  \
user_id                                                                     
22779                 9775402               9774461             9759544.0   
150224                9089120               9778661             9777492.0   
160892                9778021               9778627             9778351.0   
1001055               9776071               9776808             9776246.0   
1001055               9771995               9776583             9776553.0   
...                       ...                   ...                   ...   
2053999               9353420               9775621             9774549.0   
2053999               9770028               9775500             9486486.0   
2060487               9775648               9775325                   NaN   
2060487               9775722               9775621             9774943.0   
2096611               9771237               9770369             9726171.0   

         article_ids_inview_6  article_ids_inview_7  article_ids_inview_8  \
user_id                                                                     
22779               9773947.0             9142581.0             9775331.0   
150224              9778718.0             9778657.0             9778682.0   
160892              9778155.0             9778226.0             9777034.0   
1001055             9776497.0             9776046.0             9776855.0   
1001055             9695098.0             9776071.0             9776691.0   
...                       ...                   ...                   ...   
2053999             9771197.0             8422665.0             9775699.0   
2053999             9725048.0             9775419.0             9775478.0   
2060487                   NaN                   NaN                   NaN   
2060487             9775611.0             9775647.0             9775478.0   
2096611                   NaN                   NaN                   NaN   

         article_ids_inview

In [43]:
def create_pca_embeddings(df, columns, n_components):
    # Fill NaN values with a default value (-999)
    df_filled = df[columns].fillna(-999)
    
    # Initialize PCA model
    pca = PCA(n_components=n_components)
    
    # Fit PCA on the numerical data
    embeddings = pca.fit_transform(df_filled.values)
    
    # Create a new DataFrame to store PCA embeddings with the same index as the original DataFrame
    embeddings_df = pd.DataFrame(embeddings, index=df.index)
    
    # Rename columns of the embeddings DataFrame
    embeddings_df.columns = [f'pca_embedding_{i}' for i in range(n_components)]
    
    return embeddings_df

In [75]:
# Specify columns to apply embeddings
columns_for_embeddings = list(df_users.columns)

# Apply PCA embeddings to ID columns
df_users_embeddings = create_pca_embeddings(df_users, columns_for_embeddings, n_components=300)

In [76]:
df_users_embeddings

pca_embedding_0  pca_embedding_1  pca_embedding_2  pca_embedding_3  \
user_id                                                                       
22779       6.408010e+07    -4.088422e+07    -4.089813e+07     5.491450e+05   
150224     -7.479383e+07     1.330246e+07     1.390406e+07    -2.396311e+07   
160892      3.498216e+06    -5.695839e+07     1.264161e+07     2.579012e+07   
1001055     3.887623e+07    -5.482619e+07    -2.230824e+07     2.354616e+07   
1001055     3.857886e+07    -5.479704e+07    -2.224796e+07     2.320635e+07   
...                  ...              ...              ...              ...   
2053999    -3.071658e+07    -3.928234e+07     3.620141e+07    -5.089836e+06   
2053999    -3.099265e+07    -3.927617e+07     3.617457e+07    -5.266003e+06   
2060487     7.349914e+07    -3.265521e+07    -4.427860e+07    -1.000403e+07   
2060487     7.304990e+07    -3.262517e+07    -4.415181e+07    -1.051831e+07   
2096611     6.746052e+07    -3.831519e+07    -4.232355e+07    -2.820732e+06   

         pca_embedding_4  pca_embedding_5  pca_embedding_6  pca_embedding_7  \
user_id                                                                       
22779       2.413974e+07     5.588224e+06     4.855760e+06    -1.572036e+07   
150224      2.018129e+07    -1.333685e+07     1.501829e+07     1.012964e+07   
160892     -1.380920e+07    -7.481470e+06    -8.093821e+05     1.547762e+07   
1001055     1.711594e+07    -1.619116e+07     1.012404e+06    -1.146173e+07   
1001055     1.618197e+07    -1.401110e+07     2.307193e+07    -7.322497e+06   
...                  ...              ...              ...              ...   
2053999    -1.735704e+07     1.859297e+07     1.637483e+07    -8.606570e+05   
2053999    -1.785622e+07     1.996220e+07     3.158709e+07     1.708355e+06   
2060487     2.032542e+07     1.239543e+07    -1.032220e+07    -1.076292e+07   
2060487     1.895750e+07     1.560077e+07     2.234832e+07    -4.667682e+06   
2096611     2.339119e+07     7.480243e+06    -7.645970e+06    -1.594740e+07   

         pca_embedding_8  pca_embedding_9  pca_embedding_10  pca_embedding_11  \
user_id                                                                         
22779      -1.581353e+07     9.500986e+06      1.369380e+07      1.994485e+06   
150224      2.214202e+06    -7.558940e+06      1.237309e+07     -6.630312e+06   
160892      3.404365e+06    -1.169547e+07      4.851565e+06      8.566728e+06   
1001055     8.752896e+06     8.310791e+06     -6.899714e+06     -8.997442e+06   
1001055     8.043930e+06     8.536783e+06     -6.993961e+06     -9.331433e+06   
...                  ...              ...               ...               ...   
2053999    -1.137648e+07     1.130787e+07     -5.429338e+06     -6.367944e+06   
2053999    -1.166682e+07     1.195204e+07     -5.587265e+06     -7.359107e+06   
2060487    -1.624510e+07    -6.855981e+05      1.005355e+07      9.167921e+06   
2060487    -1.740213e+07    -5.417988e+05      9.875825e+06      9.269348e+06   
2096611    -1.636890e+07     6.575494e+06      1.340872e+07      4.312848e+06   

         pca_embedding_12  pca_embedding_13  pca_embedding_14  \
user_id                                                         
22779       -4.705240e+06     -1.129032e+07     -6.182799e+06   
150224       1.013877e+07     -5.471949e+06     -1.301113e+05   
160892      -4.185471e+06     -1.089703e+07     -6.983373e+06   
1001055      7.292381e+06     -2.498419e+06      1.191690e+07   
1001055      7.837167e+06     -4.448759e+06      1.173658e+07   
...                   ...               ...               ...   
2053999      1.102171e+07     -1.020804e+06      2.814545e+04   
2053999      2.485773e+06      2.311291e+07     -1.169649e+06   
2060487     -6.261852e+06      4.582948e+06     -1.155048e+07   
2060487     -3.078431e+06     -4.725114e+06     -1.115705e+07   
2096611     -8.460677e+06      1.659412e+06     -9.683075e+06   

         pca_embedding_15  pca_embedding_16  pca_embe

## Create user-article matrix

## Compute Interaction Matrix|:
##### Compute the recommendation score for each item i for the user u using the learned embeddings.
##### The recommendation score can be calculated as the dot product (similarity) between the user embedding u_emb and the item embedding v_i for each item i.
#### Score(𝑢,𝑖)=𝑢_𝑒𝑚𝑏^𝑇 × 𝑣𝑖

#### Where:
#### - u_emb: User embedding vector for user u.
#### - v_i: Item embedding vector for item i.
#### -  ^T: Transpose operation.
#### -  \times: Dot product.

In [77]:
# Compute user-article interaction matrix X using matrix multiplication
X = np.dot(df_users_embeddings, df_articles_embeddings.T)

# X is now a matrix of shape (N_users, N_articles) containing combined embeddings

In [83]:
X_df = pd.DataFrame(X, index = df_users_embeddings.index.values, columns = df_articles_embeddings.index.values)

In [84]:
X_df.head()

3037230       3044020       3057622       3073151       3193383  \
22779   -3.264528e+06 -6.118612e+06 -3.839643e+06 -4.367045e+06 -5.160913e+06   
150224  -4.452966e+05  1.966557e+04 -1.634151e+06 -2.978411e+05  2.634520e+05   
160892   1.373247e+06  1.263042e+06  3.465842e+05  3.465235e+06  6.603298e+06   
1001055  1.753827e+06  3.550315e+05  1.732574e+06  4.296575e+06  5.578164e+06   
1001055  4.383877e+06  1.094239e+06  3.655310e+06  5.333790e+06  6.144829e+06   

              3196611       3200325       3200913       3209311       3209357  \
22779   -6.061207e+06 -1.016577e+07 -6.769036e+06 -5.209313e+06 -8.175120e+06   
150224   8.297958e+05  1.439177e+06  2.681853e+06 -4.758778e+05  2.733125e+06   
160892   6.290421e+06  5.698727e+06  5.127314e+06  5.309111e+06  2.833916e+06   
1001055  6.407894e+06  3.226350e+06  1.927537e+06  5.532452e+06  2.750602e+06   
1001055  8.230060e+06  3.952991e+06  3.596689e+06  6.567102e+06  3.941980e+06   

              3223114       3251664       3971783       3977720       3983641  \
22779   -3.883592e+06  1.788763e+06 -3.122505e+06 -2.845592e+06 -6.790765e+06   
150224  -8.341400e+05 -2.695683e+06 -1.635256e+06 -1.972224e+06  3.966097e+06   
160892   4.413852e+06  2.790226e+06  1.899234e+06  3.272578e+06  4.449723e+06   
1001055  5.785405e+06  4.864125e+06  1.300755e+06  4.656624e+06  2.986239e+06   
1001055  8.159135e+06  8.104143e+06  3.495302e+06  6.871042e+06  5.059440e+06   

              3987418       3988589       3993395       3994264       3997229  \
22779   -7.290201e+06 -8.511357e+06 -3.057739e+06 -4.724885e+06 -7.322706e+06   
150224   1.012284e+06  5.247797e+06 -4.094767e+05 -2.988984e+05  8.395657e+05   
160892   1.532666e+06  1.764681e+06  1.909362e+06  3.861986e+06  4.172363e+06   
1001055  1.913784e+06 -1.356861e+04  2.873756e+06  4.154331e+06  3.011326e+06   
1001055  4.570509e+06  1.961910e+06  2.746035e+06  5.690506e+06  5.647307e+06   

              3997233       3998680       4000567       4000823       4003163  \
22779   -5.301001e+06 -2.423813e+06 -2.880237e+06 -2.602655e+06 -4.593987e+06   
150224   7.098054e+05  5.292064e+05 -7.772129e+05  2.232666e+06  1.332536e+06   
160892   6.182868e+06  2.017523e+06  3.620262e+06  9.669917e+05  4.631862e+06   
1001055  1.940942e+06  1.138142e+06  2.747092e+06  2.594929e+06  4.427257e+06   
1001055  3.343622e+06  5.387942e+06  4.819328e+06  5.767245e+06  5.569106e+06   

              4003362       4003431       4003926       4007811       4008213  \
22779   -5.961379e+06 -1.898561e+06  1.999793e+06 -6.204676e+06 -5.063459e+06   
150224   2.142580e+06 -2.076580e+06 -2.708028e+06 -1.376456e+06 -2.543073e+06   
160892   3.014787e+06  4.195192e+06  2.077780e+06  2.973492e+06  4.525801e+06   
1001055  3.857550e+06  3.895095e+06  3.319603e+06  4.315114e+06  2.651361e+06   
1001055  4.967606e+06  5.029521e+06  7.532357e+06  5.955368e+06  4.540623e+06   

              4009177       4014381       4021392       4024289       4024449  \
22779   -4.626837e+06 -4.774758e+06 -3.461287e+06 -3.390704e+06 -4.674278e+06   
150224   1.891762e+06  1.790943e+06 -2.530061e+05 -6.112166e+05  3.694515e+05   
160892   4.379687e+06  2.297200e+06 -1.888689e+06  2.185060e+06  1.334495e+06   
1001055  1.490107e+06  4.942889e+05  2.761802e+06  1.713412e+06  4.356594e+06   
1001055  2.728727e+06  1.708981e+06  4.812837e+06  4.397626e+06  6.549566e+06   

              4026960       4035059       4035605       4040731       4040737  \
22779   -7.098710e+06 -4.064857e+06  1.408363e+06 -4.151780e+06 -5.342792e+06   
150224   3.146747e+05  1.800432e+06 -4.216694e+06 -1.442035e+06 -3.271686e+05   
160892   6.003248e+06  3.547338e+06 -7.236253e+04  5.009066e+06  4.997221e+06   
1001055  4.118816e+06  2.325036e+06  4.271982e+06  4.771876e+06  4.889150e+06   
1001055  5.589519e+06  5.329791e+06  6.992440e+06  5.856962e+06  5.896307e+06   

              4043121       4044042       4045439       4048845       4050800  \
22779   -4.681403e+06 -7.373342e+06 -

## Recommendation Process
##### To generate recommendations for a specific user, follow these steps:

#### a) Retrieve User's Recommendations
##### Select User: Choose the target user for whom you want to generate recommendations.
#### b) Extract User's Interaction Scores
##### User's Row in X: Retrieve the row corresponding to the selected user from the matrix X. Let's denote this row as X_user.
#### c) Rank Items by Interaction Scores
##### Sort Interaction Scores: Sort the values in the X_user row in descending order. Each value represents the interaction score between the user (selected) and a specific item.
#### d) Recommend Top-N Items
##### Top-N Recommendations: Select the top-N items with the highest interaction scores from the sorted X_user row. These items are recommended to the user based on their predicted preferences.